# 猫狗大战

In [1]:
kaggle_cli_installed = False
data_downloaded = False
data_unzipped = False
data_classified_to_dir = False
outliers_removed = True

dataset_path = './data/'

In [2]:
import os
import shutil
import matplotlib.pyplot as plt
import numpy as np
%matplotlib inline

## 下载数据集

In [4]:
if not kaggle_cli_installed:
    !pip install kaggle

In [6]:
if not data_downloaded:
    #!cp kaggle.json /home/ubuntu/.kaggle
    !kaggle competitions download -c dogs-vs-cats-redux-kernels-edition -p data

test.zip: Skipping, found more recently modified local copy (use --force to force download)
train.zip: Skipping, found more recently modified local copy (use --force to force download)
sample_submission.csv: Skipping, found more recently modified local copy (use --force to force download)


d:\programdata\anaconda2\envs\keras\lib\site-packages\requests\__init__.py:80: RequestsDependencyWarning: urllib3 (1.23) or chardet (3.0.4) doesn't match a supported version!
  RequestsDependencyWarning)


## 解压数据集

In [11]:
if not data_unzipped:
    import zipfile
#     train_dataset_zip_path = './data/dogs-vs-cats-redux-kernels-edition/train.zip'
#     test_dataset_zip_path = './data/dogs-vs-cats-redux-kernels-edition/test.zip'
    
    train_dataset_zip_path = './data/train.zip'
    test_dataset_zip_path = './data/test.zip'

    def unzip(save_path, data_path, data_name):
        """
        Unzip wrapper with the same interface as _ungzip
        :param save_path: The path of the zip files
        :param data_path: Path to extract to
        :param data_name: Name of dataset
        """
        if not os.path.exists(save_path):
            print('File {} does not exist'.format(data_name))
            return

        print('Extracting data {} ...'.format(data_name))
        with zipfile.ZipFile(save_path) as zf:
            zf.extractall(data_path)
            print('Extract {} Finish!'.format(data_name))

#         print('Removing {}'.format(data_name))
#         os.remove(save_path)

    if not os.path.exists(dataset_path + 'train'):
        unzip(train_dataset_zip_path, dataset_path, 'train.zip')
    else:
        print('Found {} Data'.format('train.zip'))

    if not os.path.exists(dataset_path + 'test'):
        unzip(test_dataset_zip_path, dataset_path, 'test.zip')
    else:
        print('Found {} Data'.format('test.zip'))


Extracting data train.zip ...
Extract train.zip Finish!
Extracting data test.zip ...
Extract test.zip Finish!


## 预处理数据集

### 异常数据处理

In [13]:
# imagenet上的猫和狗的类别
dogs_categories = [
 'n02085620','n02085782','n02085936','n02086079','n02086240','n02086646','n02086910','n02087046'
,'n02087394','n02088094','n02088238','n02088364','n02088466','n02088632','n02089078','n02089867'
,'n02089973','n02090379','n02090622','n02090721','n02091032','n02091134','n02091244','n02091467'
,'n02091635','n02091831','n02092002','n02092339','n02093256','n02093428','n02093647','n02093754'
,'n02093859','n02093991','n02094114','n02094258','n02094433','n02095314','n02095570','n02095889'
,'n02096051','n02096177','n02096294','n02096437','n02096585','n02097047','n02097130','n02097209'
,'n02097298','n02097474','n02097658','n02098105','n02098286','n02098413','n02099267','n02099429'
,'n02099601','n02099712','n02099849','n02100236','n02100583','n02100735','n02100877','n02101006'
,'n02101388','n02101556','n02102040','n02102177','n02102318','n02102480','n02102973','n02104029'
,'n02104365','n02105056','n02105162','n02105251','n02105412','n02105505','n02105641','n02105855'
,'n02106030','n02106166','n02106382','n02106550','n02106662','n02107142','n02107312','n02107574'
,'n02107683','n02107908','n02108000','n02108089','n02108422','n02108551','n02108915','n02109047'
,'n02109525','n02109961','n02110063','n02110185','n02110341','n02110627','n02110806','n02110958'
,'n02111129','n02111277','n02111500','n02111889','n02112018','n02112137','n02112350','n02112706'
,'n02113023','n02113186','n02113624','n02113712','n02113799','n02113978']

cats_categories = ['n02123045','n02123159','n02123394','n02123597','n02124075','n02125311','n02127052']

# top-N
top_num = 50

In [6]:
from keras.preprocessing import image
import numpy as np

Using TensorFlow backend.


In [38]:
def is_cat_or_dog(preds):
    for pred in preds:
        if pred[0] in (dogs_categories+cats_categories):
            return True
    return False

if not outliers_removed:

    def exclude_outliers(model_name='xception', top_num=5, img_dir='train/'):
        # import models
        if model_name == 'xception':
            from keras.applications.xception import Xception, preprocess_input, decode_predictions
            model = Xception(weights='imagenet')
            img_size = (299, 299)
        elif model_name == 'inception_resnet_v2':
            from keras.applications.inception_resnet_v2 import InceptionResNetV2, preprocess_input, decode_predictions
            model = InceptionResNetV2(weights='imagenet')
            img_size = (299, 299)
        elif model_name == 'densenet201':
            from keras.applications.densenet import DenseNet201, preprocess_input, decode_predictions
            model = DenseNet201(weights='imagenet')
            img_size = (224, 224)

        img_dir = dataset_path + img_dir
        img_list = os.listdir(img_dir)
        outliers = []
        for img_name in img_list:
            if img_name == 'Thumbs.db':
                continue
            img_path = img_dir + img_name
            img = image.load_img(img_path, target_size=img_size) #os.readlink(img_path)
            x = image.img_to_array(img)
            x = np.expand_dims(x, axis=0)
            x = preprocess_input(x)

            pred = model.predict(x)
            pred = decode_predictions(pred, top=top_num)[0]
            if not is_cat_or_dog(pred):
                outliers.append(img_name)
        return outliers


#     通过generator实现
#     img_dir = dataset_path + 'some_samples/'
#     gen = image.ImageDataGenerator()
#     img_generator = gen.flow_from_directory(img_dir, target_size=img_size, shuffle=False)
#     print(img_generator)
#     preds = model.predict_generator(img_generator, verbose=1)
    
#     decode_preds = decode_predictions(preds, top=top_num)
#     outliers = []

#     for pred, filename in zip(decode_preds, img_generator.filenames):
#         print(filename)
#         print(pred)
#         print(is_cat_or_dog(pred))
#         if not is_cat_or_dog(pred):
#             outliers.append(filename)
#     return outliers

In [39]:
if not outliers_removed:
    outliers_xception = exclude_outliers(model_name='xception',top_num=top_num)
    print(outliers_xception)

['cat.9494.jpg', 'dog.9188.jpg', 'dog.1259.jpg', 'cat.7377.jpg', 'cat.8456.jpg', 'dog.1308.jpg', 'cat.5804.jpg', 'cat.2520.jpg', 'cat.2429.jpg', 'cat.2939.jpg', 'cat.4833.jpg', 'dog.8898.jpg', 'dog.1194.jpg', 'dog.12376.jpg', 'dog.4367.jpg', 'cat.5418.jpg', 'cat.10636.jpg', 'dog.10747.jpg', 'cat.12476.jpg', 'cat.4688.jpg', 'cat.5492.jpg', 'cat.2337.jpg', 'dog.6475.jpg', 'cat.519.jpg', 'dog.8736.jpg', 'cat.5609.jpg', 'cat.11237.jpg', 'dog.12155.jpg', 'cat.8286.jpg', 'cat.10029.jpg', 'cat.11607.jpg', 'cat.10712.jpg', 'dog.2614.jpg', 'dog.10190.jpg', 'cat.4308.jpg', 'cat.5351.jpg', 'dog.1773.jpg', 'dog.10237.jpg', 'cat.8470.jpg', 'cat.4338.jpg', 'cat.5071.jpg', 'cat.3672.jpg', 'cat.6696.jpg', 'cat.10176.jpg', 'dog.10801.jpg', 'dog.6725.jpg', 'cat.9171.jpg', 'cat.3123.jpg', 'cat.12272.jpg', 'cat.7682.jpg', 'dog.9517.jpg', 'cat.7564.jpg', 'cat.6590.jpg', 'cat.8921.jpg', 'cat.10365.jpg', 'cat.7968.jpg', 'cat.12424.jpg', 'cat.3216.jpg', 'dog.11299.jpg', 'dog.10161.jpg', 'dog.2422.jpg', 'dog.3

In [40]:
if not outliers_removed:
    outliers_inception_resnet_v2 = exclude_outliers(model_name='inception_resnet_v2',top_num=top_num)
    print(outliers_inception_resnet_v2)

['cat.10084.jpg', 'cat.12182.jpg', 'dog.9188.jpg', 'dog.1259.jpg', 'cat.7377.jpg', 'cat.10945.jpg', 'cat.8456.jpg', 'dog.1308.jpg', 'cat.1747.jpg', 'cat.2520.jpg', 'cat.2939.jpg', 'cat.5816.jpg', 'cat.4355.jpg', 'dog.1194.jpg', 'dog.12376.jpg', 'dog.4367.jpg', 'cat.5418.jpg', 'cat.11661.jpg', 'cat.1928.jpg', 'dog.10747.jpg', 'cat.4353.jpg', 'cat.4688.jpg', 'cat.4503.jpg', 'dog.6475.jpg', 'cat.10700.jpg', 'cat.12380.jpg', 'cat.11777.jpg', 'dog.8736.jpg', 'cat.7464.jpg', 'cat.388.jpg', 'cat.6573.jpg', 'dog.1043.jpg', 'cat.6345.jpg', 'cat.7976.jpg', 'cat.124.jpg', 'cat.9377.jpg', 'cat.3658.jpg', 'cat.3004.jpg', 'dog.12155.jpg', 'cat.11256.jpg', 'cat.6754.jpg', 'cat.10029.jpg', 'cat.4824.jpg', 'cat.10712.jpg', 'dog.2614.jpg', 'cat.4198.jpg', 'cat.4906.jpg', 'dog.10190.jpg', 'cat.4308.jpg', 'cat.5351.jpg', 'cat.2598.jpg', 'dog.1773.jpg', 'dog.10237.jpg', 'cat.8470.jpg', 'cat.4338.jpg', 'cat.5071.jpg', 'cat.11159.jpg', 'cat.7728.jpg', 'cat.9360.jpg', 'cat.6451.jpg', 'cat.3672.jpg', 'cat.5843

In [41]:
if not outliers_removed:
    outliers_densenet201 = exclude_outliers(model_name='densenet201',top_num=top_num)
    print(outliers_densenet201)

['dog.9188.jpg', 'dog.1259.jpg', 'cat.7377.jpg', 'cat.8456.jpg', 'cat.1747.jpg', 'cat.5804.jpg', 'cat.2520.jpg', 'cat.2429.jpg', 'cat.2939.jpg', 'cat.4355.jpg', 'cat.10749.jpg', 'dog.1194.jpg', 'dog.12376.jpg', 'dog.4367.jpg', 'cat.5418.jpg', 'cat.4688.jpg', 'cat.5324.jpg', 'dog.6475.jpg', 'cat.11777.jpg', 'dog.8736.jpg', 'dog.1043.jpg', 'dog.4127.jpg', 'cat.3004.jpg', 'cat.461.jpg', 'dog.4507.jpg', 'cat.6503.jpg', 'cat.10029.jpg', 'cat.10712.jpg', 'dog.2614.jpg', 'dog.10190.jpg', 'cat.5351.jpg', 'dog.1773.jpg', 'dog.10237.jpg', 'cat.8614.jpg', 'cat.4338.jpg', 'cat.343.jpg', 'cat.3672.jpg', 'cat.7964.jpg', 'cat.8417.jpg', 'cat.3911.jpg', 'cat.5939.jpg', 'cat.10176.jpg', 'dog.10801.jpg', 'cat.6348.jpg', 'dog.6725.jpg', 'cat.5456.jpg', 'cat.714.jpg', 'cat.12272.jpg', 'cat.7682.jpg', 'cat.9983.jpg', 'dog.9517.jpg', 'cat.7564.jpg', 'cat.10365.jpg', 'cat.7968.jpg', 'cat.3216.jpg', 'cat.901.jpg', 'dog.11299.jpg', 'dog.10161.jpg', 'dog.2422.jpg', 'cat.2496.jpg', 'dog.3889.jpg', 'cat.8087.jpg'

In [42]:
if not outliers_removed:
    outliers = list(set(outliers_xception+outliers_inception_resnet_v2+ outliers_densenet201))
    print(outliers)
    
    outliers_file_path = './outliers.txt'

    if os.path.isfile(outliers_file_path):
        os.remove(outliers_file_path)
    with open(outliers_file_path, 'w') as f:
        f.write('\n'.join(outliers))


['cat.3911.jpg', 'cat.7728.jpg', 'dog.4367.jpg', 'dog.6475.jpg', 'cat.6451.jpg', 'cat.8286.jpg', 'dog.1895.jpg', 'cat.9163.jpg', 'cat.5939.jpg', 'cat.10084.jpg', 'cat.7564.jpg', 'cat.1747.jpg', 'cat.9171.jpg', 'dog.1259.jpg', 'cat.3658.jpg', 'cat.461.jpg', 'cat.8470.jpg', 'cat.8921.jpg', 'cat.10700.jpg', 'dog.10237.jpg', 'cat.12073.jpg', 'cat.4833.jpg', 'cat.388.jpg', 'dog.4127.jpg', 'cat.9731.jpg', 'cat.7983.jpg', 'cat.2429.jpg', 'cat.6590.jpg', 'dog.2578.jpg', 'cat.4355.jpg', 'cat.1928.jpg', 'cat.10636.jpg', 'cat.12272.jpg', 'cat.7976.jpg', 'dog.12155.jpg', 'cat.3004.jpg', 'cat.2457.jpg', 'cat.10365.jpg', 'cat.3123.jpg', 'cat.3868.jpg', 'dog.9188.jpg', 'cat.6822.jpg', 'cat.11969.jpg', 'cat.10276.jpg', 'cat.11256.jpg', 'cat.8417.jpg', 'cat.8087.jpg', 'cat.7377.jpg', 'cat.9494.jpg', 'dog.10747.jpg', 'dog.2422.jpg', 'cat.2337.jpg', 'cat.376.jpg', 'dog.5604.jpg', 'cat.4906.jpg', 'dog.6725.jpg', 'cat.4353.jpg', 'cat.6503.jpg', 'dog.8898.jpg', 'cat.10712.jpg', 'dog.7076.jpg', 'cat.5351.jpg

### 获取异常值


In [33]:
if not outliers_removed:
    outliers_file_path = './outliers.txt'
    with open(outliers_file_path, 'r') as f:
        outliers_str = f.read()
        outliers = outliers_str.split('\n')
        print(outliers)

['cat.3911.jpg', 'cat.7728.jpg', 'dog.4367.jpg', 'dog.6475.jpg', 'cat.6451.jpg', 'cat.8286.jpg', 'dog.1895.jpg', 'cat.9163.jpg', 'cat.5939.jpg', 'cat.10084.jpg', 'cat.7564.jpg', 'cat.1747.jpg', 'cat.9171.jpg', 'dog.1259.jpg', 'cat.3658.jpg', 'cat.461.jpg', 'cat.8470.jpg', 'cat.8921.jpg', 'cat.10700.jpg', 'dog.10237.jpg', 'cat.12073.jpg', 'cat.4833.jpg', 'cat.388.jpg', 'dog.4127.jpg', 'cat.9731.jpg', 'cat.7983.jpg', 'cat.2429.jpg', 'cat.6590.jpg', 'dog.2578.jpg', 'cat.4355.jpg', 'cat.1928.jpg', 'cat.10636.jpg', 'cat.12272.jpg', 'cat.7976.jpg', 'dog.12155.jpg', 'cat.3004.jpg', 'cat.2457.jpg', 'cat.10365.jpg', 'cat.3123.jpg', 'cat.3868.jpg', 'dog.9188.jpg', 'cat.6822.jpg', 'cat.11969.jpg', 'cat.10276.jpg', 'cat.11256.jpg', 'cat.8417.jpg', 'cat.8087.jpg', 'cat.7377.jpg', 'cat.9494.jpg', 'dog.10747.jpg', 'dog.2422.jpg', 'cat.2337.jpg', 'cat.376.jpg', 'dog.5604.jpg', 'cat.4906.jpg', 'dog.6725.jpg', 'cat.4353.jpg', 'cat.6503.jpg', 'dog.8898.jpg', 'cat.10712.jpg', 'dog.7076.jpg', 'cat.5351.jpg

In [4]:
def align_figures():
    import matplotlib
    from matplotlib._pylab_helpers import Gcf
    from IPython.display import display_html
    import base64
    from ipykernel.pylab.backend_inline import show

    images = []
    for figure_manager in Gcf.get_all_fig_managers():
        fig = figure_manager.canvas.figure
        png = get_ipython().display_formatter.format(fig)[0]['image/png']
        src = base64.encodebytes(png).decode()
        images.append('<img style="margin:0" align="left" src="data:image/png;base64,{}"/>'.format(src))

    html = "<div>{}</div>".format("".join(images))
    show._draw_called = False
    matplotlib.pyplot.close('all')
    display_html(html, raw=True)
    
def show_images(img_list, img_path, col_num=5):
    plt.figure(dpi=150)
    for i in range(len(img_list)):
        img = plt.imread(img_path+img_list[i])
        plt.subplot(len(img_list)//col_num+1, col_num, i+1)
        plt.title(img_list[i], fontsize=8)
        plt.axis('off')
        plt.imshow(img)
    align_figures()

In [35]:
show_num = 10
for i in range(len(outliers)//show_num+1):
    show_images(outliers[i*show_num:(i+1)*show_num], dataset_path+'train/',5)

# img_path_temp = dataset_path+'train/'
# img_list_temp = os.listdir(img_path_temp)
# show_images(img_list_temp[:60], img_path_temp, 5)


根据上面的图片，手动排除正确的猫狗，将真正的异常值写入`real_outliers.txt`文件

#### 读取正确的异常值

In [5]:
with open('real_outliers.txt','r') as f:
    real_outliers = f.read()
    real_outliers = real_outliers.split('\n')
show_num = 10
print(len(real_outliers))
print(real_outliers)


56
['dog.4367.jpg', 'dog.6475.jpg', 'cat.7564.jpg', 'cat.9171.jpg', 'cat.3658.jpg', 'cat.8921.jpg', 'cat.10700.jpg', 'dog.4127.jpg', 'dog.2578.jpg', 'cat.10636.jpg', 'cat.12272.jpg', 'dog.12155.jpg', 'cat.2457.jpg', 'cat.10365.jpg', 'cat.3868.jpg', 'cat.6822.jpg', 'cat.8087.jpg', 'cat.7377.jpg', 'dog.10747.jpg', 'cat.2337.jpg', 'dog.5604.jpg', 'dog.6725.jpg', 'dog.8898.jpg', 'cat.10712.jpg', 'dog.7076.jpg', 'cat.5351.jpg', 'cat.10029.jpg', 'cat.7372.jpg', 'dog.12376.jpg', 'cat.3672.jpg', 'cat.12476.jpg', 'dog.9517.jpg', 'cat.4308.jpg', 'dog.1043.jpg', 'dog.3889.jpg', 'cat.11184.jpg', 'dog.12148.jpg', 'dog.1308.jpg', 'dog.11266.jpg', 'dog.1773.jpg', 'dog.10801.jpg', 'cat.5418.jpg', 'dog.11299.jpg', 'cat.8456.jpg', 'cat.4338.jpg', 'dog.4507.jpg', 'dog.9418.jpg', 'dog.10190.jpg', 'cat.4688.jpg', 'dog.2614.jpg', 'dog.8736.jpg', 'cat.3216.jpg', 'cat.2520.jpg', 'cat.11607.jpg', 'dog.1194.jpg', 'dog.10161.jpg']


In [6]:
# 查看确认正确性
for i in range(len(real_outliers)//show_num+1):
    show_images(real_outliers[i*show_num:(i+1)*show_num], dataset_path+'train/',5)

### 创建猫狗分类文件夹

In [26]:
if not data_classified_to_dir:
    #  创建train2/dog及train2/cat文件夹
    if not os.path.exists(dataset_path + 'train2/dog'):
        os.makedirs(dataset_path+'train2/dog')
        print('Directory "train2/dog" created!')
    else:
        print('Directory "train2/dog" exists!')
        
    if not os.path.exists(dataset_path + 'val2/dog'):
        os.makedirs(dataset_path+'val2/dog')
        print('Directory "val2/dog" created!')
    else:
        print('Directory "val2/dog" exists!')

    if not os.path.exists(dataset_path + 'train2/cat'):
        os.makedirs(dataset_path+'train2/cat')
        print('Directory "train2/cat" created!')
    else:
        print('Directory "train2/cat" exists!')
        
    if not os.path.exists(dataset_path + 'val2/cat'):
        os.makedirs(dataset_path+'val2/cat')
        print('Directory "val2/cat" created!')
    else:
        print('Directory "val2/cat" exists!')

    # 创建test2/test文件夹
    # if not os.path.exists(dataset_path + 'test2/test'):
    #     os.makedirs(dataset_path+'test2/test')
    #     print('Directory "test2/test" created!')
    # else:
    #     print('Directory "test2/test" exists!')


Directory "train2/dog" created!
Directory "val2/dog" exists!
Directory "train2/cat" created!
Directory "val2/cat" exists!


### 对文件进行分类，并排除异常值

In [10]:
if not data_classified_to_dir:
    from sklearn.model_selection import train_test_split
   
    val_fraction = 0.2
    
    # 对训练文件名进行分类
    train_filenames = os.listdir(dataset_path + 'train')
    cat_filenames = filter(lambda x: x[:3] == 'cat', train_filenames)
    dog_filenames = filter(lambda x: x[:3] == 'dog', train_filenames)
    
    # 删除异常值
    cat_filenames = np.array([filename for filename in cat_filenames if filename not in real_outliers])
    dog_filenames = np.array([filename for filename in dog_filenames if filename not in real_outliers])
    
    # 分割训练集与验证集
    train_cat, val_cat = train_test_split(cat_filenames, test_size=val_fraction)
    train_dog, val_dog = train_test_split(dog_filenames, test_size=val_fraction)
    
    if len(os.listdir(dataset_path + 'train2/cat/')) != len(train_cat) :
        for filename in train_cat:
            if os.path.isfile(dataset_path+'train2/cat/'+filename):
                os.unlink(dataset_path+'train2/cat/'+filename)
            os.symlink(dataset_path+'train/'+filename, dataset_path+'train2/cat/'+filename)
        print('train cat symlink success')
    else:
        print('train cat symlink exists')
    
    
    if len(os.listdir(dataset_path + 'val2/cat/')) != len(val_cat):
        for filename in val_cat:
            if os.path.isfile(dataset_path+'val2/cat/'+filename):
                os.unlink(dataset_path+'val2/cat/'+filename)
            os.symlink(dataset_path+'train/'+filename, dataset_path+'val2/cat/'+filename)
        
        print('val cat symlink success')
    else:
        print('val cat symlink exists')
        
    
    if len(os.listdir(dataset_path + 'train2/dog/')) != len(train_dog):
        for filename in train_dog:
            if os.path.isfile(dataset_path+'train2/dog/'+filename):
                os.unlink(dataset_path+'train2/dog/'+filename)
            os.symlink(dataset_path+'train/'+filename, dataset_path+'train2/dog/'+filename)
        print('train dog symlink success')
    else:
        print('train dog symlink exists')
        
        
    if len(os.listdir(dataset_path + 'val2/dog/')) != len(val_dog): 
        for filename in val_dog:
            if os.path.isfile(dataset_path+'val2/dog/'+filename):
                os.unlink(dataset_path+'val2/dog/'+filename)
            os.symlink(dataset_path+'train/'+filename, dataset_path+'val2/dog/'+filename)
                
        print('val dog symlink success')
    else:
        print('val dog symlink exists')
    # 对测试文件进行关联
    # os.symlink(dataset_path+'test', dataset_path+'test2/test')


train cat symlink exists
val cat symlink exists
train dog symlink exists
val dog symlink exists


In [8]:
if not data_classified_to_dir:
    from shutil import copyfile
    
     #  创建train2/dog及train2/cat文件夹
    if not os.path.exists(dataset_path + 'train3/cat'):
        os.makedirs(dataset_path+'train3/cat')
        print('Directory "train3/cat" created!')
    else:
        print('Directory "train3/cat" exists!')
        
        
    if not os.path.exists(dataset_path + 'train3/dog'):
        os.makedirs(dataset_path+'train3/dog')
        print('Directory "train3/dog" created!')
    else:
        print('Directory "train3/dog" exists!')
    
    train_filenames = os.listdir(dataset_path + 'train')
    cat_filenames = filter(lambda x: x[:3] == 'cat', train_filenames)
    dog_filenames = filter(lambda x: x[:3] == 'dog', train_filenames)
    
    # 删除异常值
    cat_filenames = np.array([filename for filename in cat_filenames if filename not in real_outliers])
    dog_filenames = np.array([filename for filename in dog_filenames if filename not in real_outliers])
    
    print('Number of Cat files:', len(cat_filenames))
    print('Number of Dog files:', len(dog_filenames))
    
    if len(os.listdir(dataset_path + 'train3/cat/')) <=0 :
        for filename in cat_filenames:
            if os.path.isfile(dataset_path+'train3/cat/'+filename):
                os.unlink(dataset_path+'train3/cat/'+filename)
#             os.symlink(dataset_path+'train/'+filename, dataset_path+'train3/cat/'+filename)
            copyfile(dataset_path+'train/'+filename, dataset_path+'train3/cat/'+filename)
        print('train cat copyfile success')
    else:
        print('train cat files exists')
        
    if len(os.listdir(dataset_path + 'train3/dog/')) <=0:
        for filename in dog_filenames:
            if os.path.isfile(dataset_path+'train3/dog/'+filename):
                os.unlink(dataset_path+'train3/dog/'+filename)
#             os.symlink(dataset_path+'train/'+filename, dataset_path+'train3/dog/'+filename)
            copyfile(dataset_path+'train/'+filename, dataset_path+'train3/dog/'+filename)
        print('train dog copyfile success')
    else:
        print('train dog files exists')

Directory "train3/cat" created!
Directory "train3/dog" created!
Number of Cat files: 12471
Number of Dog files: 12473
train cat copyfile success
train dog copyfile success


In [41]:
# 显示目录结构
#省略文件名
!tree  ./data/train2 
# !tree  ./data/train2 /f 

卷 资料 的文件夹 PATH 列表
卷序列号为 0007-DAC2
E:\PYTHON\UDACITY\CAPSTONE\DOG_VS_CAT\DATA\TRAIN2
├─cat
└─dog


## 单模型迁移学习

### Xception迁移学习

In [ ]:
# from keras.applications.xception import Xception

### InceptionV3迁移学习

In [9]:
from keras.applications.inception_v3 import InceptionV3
from keras.preprocessing import image
from keras.models import Model
from keras.layers import Dense, GlobalAveragePooling2D
from keras import backend as K

# don't use ImageDataGenerator validation_split parameter
# train_gen = image.ImageDataGenerator()
# val_gen = image.ImageDataGenerator()

# train_gen.flow_from_directory(dataset_path+'train2/', target_size=(299,299), shuffle=True, batch_size=16)
# val_gen.flow_from_directory(dataset_path+'val2/', target_size=(299,299), shuffle=True, batch_size=16)

# use ImageDataGenerator validation_split parameter
gen = image.ImageDataGenerator(validation_split=0.2)

train_gen = gen.flow_from_directory(dataset_path+'train3/', target_size=(299,299), shuffle=True, batch_size=16, subset='training', follow_links=True, class_mode='binary')
val_gen = gen.flow_from_directory(dataset_path+'train3/', target_size=(299,299), shuffle=True, batch_size=16, subset='validation', follow_links=True, class_mode='binary')



D:\ProgramData\Anaconda2\envs\keras\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


Found 19956 images belonging to 2 classes.
Found 4988 images belonging to 2 classes.


In [10]:
base_model = InceptionV3(weights='imagenet', include_top=False)

x = base_model.output
x = GlobalAveragePooling2D()(x)

x = Dense(1024, activation='relu')(x)

predictions = Dense(1, activation='sigmoid')(x)

model = Model(inputs=base_model.inputs, outputs=predictions)


for layer in base_model.layers:
    layer.trainable = False


model.compile(optimizer="adam", loss='binary_crossentropy', metrics=['accuracy'])
print('训练新增的全链接层: ')
model.fit_generator(train_gen, epochs=1, verbose=1, validation_data=val_gen, steps_per_epoch=25000//16)


训练新增的全链接层: 
Epoch 1/1
   2/1562 [..............................] - ETA: 12:58:04 - loss: 0.8791 - acc: 0.5312

KeyboardInterrupt: 

In [44]:
import pandas as pd
from keras.preprocessing.image import *
from keras.applications.inception_v3 import preprocess_input
df = pd.read_csv("./data/sample_submission.csv")

# test_gen = ImageDataGenerator()
# test_generator = test_gen.flow_from_directory("./data/test", (299, 299), shuffle=False, 
#                                          batch_size=16, class_mode='binary')

# y_pred = model.predict_generator(test_generator,  verbose=1,  steps=25000//16)

test_images = os.listdir('./data/test')

for i in range(len(test_images)):
    
    img_path = './data/test/{}.jpg'.format(i+1)
#     print(img_path)
    img = image.load_img(img_path, target_size=(299, 299))
    x = image.img_to_array(img)
    x = np.expand_dims(x, axis=0)
    x = preprocess_input(x)
    
    preds = model.predict(x)
    
#     index = int(fname[fname.rfind('/')+1:fname.rfind('.')])
    df.set_value(i, 'label', preds)
    if i % 1000 == 0:
        print('{} predicted'.format(i+1))

print('predict finished')
df.to_csv('pred.csv', index=None)
df.head(10)

/home/ubuntu/anaconda3/envs/tensorflow_p36/lib/python3.6/site-packages/ipykernel/__main__.py:26: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead


1 predicted
101 predicted
201 predicted
301 predicted
401 predicted
501 predicted
601 predicted
701 predicted
801 predicted
901 predicted
1001 predicted
1101 predicted
1201 predicted
1301 predicted
1401 predicted
1501 predicted
1601 predicted
1701 predicted
1801 predicted
1901 predicted
2001 predicted
2101 predicted
2201 predicted
2301 predicted
2401 predicted
2501 predicted
2601 predicted
2701 predicted
2801 predicted
2901 predicted
3001 predicted
3101 predicted
3201 predicted
3301 predicted
3401 predicted
3501 predicted
3601 predicted
3701 predicted
3801 predicted
3901 predicted
4001 predicted
4101 predicted
4201 predicted
4301 predicted
4401 predicted
4501 predicted
4601 predicted
4701 predicted
4801 predicted
4901 predicted
5001 predicted
5101 predicted
5201 predicted
5301 predicted
5401 predicted
5501 predicted
5601 predicted
5701 predicted
5801 predicted
5901 predicted
6001 predicted
6101 predicted
6201 predicted
6301 predicted
6401 predicted
6501 predicted
6601 predicted
6701 pr

id         label
0   1  3.906065e-36
1   2  3.504956e-21
2   3  9.908824e-24
3   4  2.948364e-28
4   5  5.191309e-34
5   6  1.044822e-37
6   7  3.941299e-36
7   8  0.000000e+00
8   9  0.000000e+00
9  10  7.271052e-32

In [ ]:

for i, layer in enumerate(base_model.layers):
    print(i, layer.name)
    
for layer in model.layers[:249]:
    layer.trainable = False

for layer in model.layers[249:]:
    layer.trainable = True
    
model.compile(optimizer='adam', loss='binary_crossentropy')
print('finetune: ')
model.fit_generator(train_gen, epochs=1, verbose=1, validation_data=val_gen)


### DenseNet121迁移学习